In [1]:
import numpy as np
import _pickle as cPickle
import os
import gzip
import matplotlib.pyplot as plt

# First exercise: Classifying MNIST with MLPs
In this exercise you will implement a Neural Network (or MLP) and classify the MNIST digits with it.
MNIST is a "well hung" dataset that has been used a lot over the years to benchmark different classification algorithms. 
To learn more about it have a look here: http://yann.lecun.com/exdb/mnist/ .

# Data Loading
We first define a function for downloading and loading MNIST.
**WARNING**: Executing it will obviously use up some space on your machine ;). 

In [2]:
def mnist(datasets_dir='./data'):
    if not os.path.exists(datasets_dir):
        os.mkdir(datasets_dir)
    data_file = os.path.join(datasets_dir, 'mnist.pkl.gz')
    if not os.path.exists(data_file):
        print('... downloading MNIST from the web')
        try:
            import urllib
            urllib.urlretrieve('http://google.com')
        except AttributeError:
            import urllib.request as urllib
        url = 'http://www.iro.umontreal.ca/~lisa/deep/data/mnist/mnist.pkl.gz'
        urllib.urlretrieve(url, data_file)

    print('... loading data')
    # Load the dataset
    f = gzip.open(data_file, 'rb')
    try:
        train_set, valid_set, test_set = cPickle.load(f, encoding="latin1")
    except TypeError:
        train_set, valid_set, test_set = cPickle.load(f)
    f.close()

    test_x, test_y = test_set
    test_x = test_x.astype('float32')
    test_x = test_x.astype('float32').reshape(test_x.shape[0], 1, 28, 28)
    test_y = test_y.astype('int32')
    valid_x, valid_y = valid_set
    valid_x = valid_x.astype('float32')
    valid_x = valid_x.astype('float32').reshape(valid_x.shape[0], 1, 28, 28)
    valid_y = valid_y.astype('int32')
    train_x, train_y = train_set
    train_x = train_x.astype('float32').reshape(train_x.shape[0], 1, 28, 28)
    train_y = train_y.astype('int32')
    rval = [(train_x, train_y), (valid_x, valid_y), (test_x, test_y)]
    print('... done loading data')
    return rval

# Neural Network Layers
We now define "bare bone" neural network layers.
The parts marked with **TODO** are where you should finish the implementation!
Conceptually we will implement the layers as follows:

Each layer has a constructor that takes an input layer plus some additional arguments such as layer size and the activation function name. The layer then uses the provided input layer to compute the layer dimensions, weight shapes, etc. and setup all auxilliary variables.

Each layer then has to provide three functions (as defined in the Layer class below): *output_shape()*, *fprop()* and *brop()*. The output_shape function is used to figure out the shape for the next layer and the *fprop()/bprop()* functions are used to compute forward and backward passes through the network.

In [3]:
# start by defining simple helpers
def sigmoid(x):
    return 1.0/(1.0+np.exp(-x))

def sigmoid_d(x):
    
    return sigmoid(x)*(1.0-sigmoid(x))

def tanh(x):
    return np.tanh(x)

def tanh_d(x):
    
    return 1.0 - tanh(x)**2

def relu(x):
    return np.maximum(0.0, x)

def relu_d(x):
    x[x<= 0] = 0.0
    x[x> 0] = 1.0
    return x
    #return 1 if (x>0) else 0

def softmax(x, axis=1):
    # to make the softmax a "safe" operation we will 
    # first subtract the maximum along the specified axis
    # so that np.exp(x) does not blow up!
    # Note that this does not change the output.
    x_max = np.max(x, axis=axis, keepdims=True)
    x_safe = x - x_max
    e_x = np.exp(x_safe)
    return e_x / np.sum(e_x, axis=axis, keepdims=True)

def one_hot(labels):
    """this creates a one hot encoding from a flat vector:
    i.e. given y = [0,2,1]
     it creates y_one_hot = [[1,0,0], [0,0,1], [0,1,0]]
    """
    classes = np.unique(labels)
    n_classes = classes.size
    one_hot_labels = np.zeros(labels.shape + (n_classes,))
    for c in classes:
        one_hot_labels[labels == c, c] = 1
    return one_hot_labels

def unhot(one_hot_labels):
    """ Invert a one hot encoding, creating a flat vector """
    return np.argmax(one_hot_labels, axis=-1)

# then define an activation function class
class Activation(object):
    
    def __init__(self, tname):
        if tname == 'sigmoid':
            self.act = sigmoid
            self.act_d = sigmoid_d
        elif tname == 'tanh':
            self.act = tanh
            self.act_d = tanh_d
        elif tname == 'relu':
            self.act = relu
            self.act_d = relu_d
        else:
            raise ValueError('Invalid activation function.')
            
    def fprop(self, input):
        # we need to remember the last input
        # so that we can calculate the derivative with respect
        # to it later on
        self.last_input = input
        return self.act(input)
    
    def bprop(self, output_grad):
        return output_grad * self.act_d(self.last_input)

# define a base class for layers
class Layer(object):
    
    def fprop(self, input):
        """ Calculate layer output for given input 
            (forward propagation). 
        """
        raise NotImplementedError('This is an interface class, please use a derived instance')

    def bprop(self, output_grad):
        """ Calculate input gradient and gradient 
            with respect to weights and bias (backpropagation). 
        """
        raise NotImplementedError('This is an interface class, please use a derived instance')

    def output_size(self):
        """ Calculate size of this layer's output.
        input_shape[0] is the number of samples in the input.
        input_shape[1:] is the shape of the feature.
        """
        raise NotImplementedError('This is an interface class, please use a derived instance')

# define a base class for loss outputs
# an output layer can then simply be derived
# from both Layer and Loss 
class Loss(object):

    def loss(self, output, output_net):
        """ Calculate mean loss given real output and network output. """
        raise NotImplementedError('This is an interface class, please use a derived instance')

    def input_grad(self, output, output_net):
        """ Calculate input gradient real output and network output. """
        raise NotImplementedError('This is an interface class, please use a derived instance')

# define a base class for parameterized things        
class Parameterized(object):
    
    def params(self):
        """ Return parameters (by reference) """
        raise NotImplementedError('This is an interface class, please use a derived instance')
    
    def grad_params(self):
        """ Return accumulated gradient with respect to params. """
        raise NotImplementedError('This is an interface class, please use a derived instance')

# define a container for providing input to the network
class InputLayer(Layer):
    
    def __init__(self, input_shape):
        if not isinstance(input_shape, tuple):
            raise ValueError("InputLayer requires input_shape as a tuple")
        self.input_shape = input_shape

    def output_size(self):
        return self.input_shape
    
    def fprop(self, input):
        return input
    
    def bprop(self, output_grad):
        return output_grad
        
class FullyConnectedLayer(Layer, Parameterized):
    """ A standard fully connected hidden layer, as discussed in the lecture.
    """
    
    def __init__(self, input_layer, num_units, 
                 init_stddev, activation_fun=Activation('relu')):
        self.num_units = num_units
        self.activation_fun = activation_fun
        # the input shape will be of size (batch_size, num_units_prev) 
        # where num_units_prev is the number of units in the input 
        # (previous) layer
        self.input_shape = input_layer.output_size()
        
        self.W = np.random.normal(0, init_stddev, (self.input_shape[1],num_units))
        #could also be initialised with a little variation of np.sqrt(2/(num_units_prev + num_units))
        #to avoid slow convergence and not keep oscillating around the minima   
        
        # and this is the bias vector of shape: (num_units)
        self.b = np.random.normal(0, init_stddev, num_units) 
        
        # create dummy variables for parameter gradients
        # no need to change these here!
        self.dW = None
        self.db = None
    
    def output_size(self):
        return (self.input_shape[0], self.num_units)
    
    def fprop(self, input):
        
        # you again want to cache the last_input for the bprop
        # implementation below!
        
        self.last_input = input
        
        if self.activation_fun == None:  
            return input.dot(self.W) + self.b
        else:
            return self.activation_fun.fprop(input.dot(self.W) + self.b)
        
        
    def bprop(self, output_grad):
        """ Calculate input gradient (backpropagation). """
        
        print("called bprop")
        
        # HINT: you may have to divide dW and db by n
        #       to make gradient checking work 
        #       OR you divide the gradient in the output layer by n        
        
        n = output_grad.shape[0]
        
        # accumulate gradient wrt. the parameters first
        # we will need to store these to later update
        # the network after a few forward backward passes
        # NOTE: you should also handle the case were 
        #       activation_fun is None (meaning no activation)
        # the gradient wrt. W should be stored as self.dW
        # the gradient wrt. b should be stored as selfdb
        if self.activation_fun == None:
            grad = output_grad
        else:
            grad = self.activation_fun.bprop(output_grad)
        
        
        # NOTE: self.dW is also a numpy dot product
        
        self.dW = np.true_divide(self.last_input.T.dot(grad),n)        
        self.db = np.true_divide(np.sum(grad, axis=0),n)
        
        # the gradient wrt. the input should be calculated here
        grad_input = (self.W.dot(grad.T)).T
        #not sure about the last transpose
        
        return grad_input
        
    def params(self):
        return self.W, self.b

    def grad_params(self):
        return self.dW, self.db

# finally we specify the interface for output layers 
# which are layers that also have a loss function
# we will implement two output layers:
#  a Linear, and Softmax (Logistic Regression) layer
# The difference between output layers and and normal 
# layers is that they will be called to compute the gradient
# of the loss through input_grad(). bprop will never 
# be called on them!
class LinearOutput(Layer, Loss):
    """ A simple linear output layer that  
        uses a squared loss (e.g. should be used for regression)
    """
    def __init__(self, input_layer):
        self.input_size = input_layer.output_size()
        
    def output_size(self):
        return (1,)
        
    def fprop(self, input):
        return input

    def bprop(self, output_grad):
        raise NotImplementedError(
            'LinearOutput should only be used as the last layer of a Network'
            + ' bprop() should thus never be called on it!'
        )
    
    def input_grad(self, Y, Y_pred):
        input_grad = np.multiply(Y_pred - Y, self.input)
        return input_grad

    def loss(self, Y, Y_pred):
        loss = 0.5 * np.square(Y_pred - Y)
        return np.mean(np.sum(loss, axis=1))

class SoftmaxOutput(Layer, Loss):
    """ A softmax output layer that calculates 
        the negative log likelihood as loss
        and should be used for classification.
    """
    
    def __init__(self, input_layer):
        self.input_size = input_layer.output_size()
        
    def output_size(self):
        return (1,)
    
    def fprop(self, input):
        return softmax(input)
    
    def bprop(self, output_grad):
        raise NotImplementedError(
            'SoftmaxOutput should only be used as the last layer of a Network'
            + ' bprop() should thus never be called on it!'
        )
    
    def input_grad(self, Y, Y_pred):
        # HINT: since this would involve taking the log 
        #       of the softmax (which is np.exp(x)/np.sum(x, axis=1))
        #       this gradient computation can be simplified a lot,
        #       you may find a connection to the LinearOutput layer!
        
        m = Y.shape[0]
        
        grad = Y_pred - Y
        
        return grad

    def loss(self, Y, Y_pred):
        # Assume one-hot encoding of Y
        out = Y_pred
        # to make the loss numerically stable 
        # you should add an epsilon in the log ;)
        eps = 1e-10        
        loss = np.sum(-np.log(out + eps) * Y, axis = 1)
        return np.mean(loss)
        

# Neural Network class
With all layers in place (and properly implemented by you) we can finally define a neural network.
For our purposes a neural network is simply a collection of layers which we will cycle through and on which we will call fprop and bprop to compute partial derivatives with respect to the input and the parameters.

Pay special attention to the *check_gradients()* function in which you should implement automatic differentiation. This function will become your best friend when checking the correctness of your implementation.

In [4]:

class NeuralNetwork:
    """ Our Neural Network container class.
    """
    def __init__(self, layers):
        self.layers = layers
        
    def _loss(self, X, Y):
        Y_pred = self.predict(X)
        return self.layers[-1].loss(Y, Y_pred)

    def predict(self, X):
        """ Calculate an output Y for the given input X. """
        
        Y_pred = X;         #Propagated value: initially X
    
        for layer in self.layers:            
            Y_pred = layer.fprop(Y_pred)
        

        return Y_pred
    
    def backpropagate(self, Y, Y_pred, upto=0):
        """ Backpropagation of partial derivatives through 
            the complete network up to layer 'upto'
        """
        next_grad = self.layers[-1].input_grad(Y, Y_pred)
        
        for i in range (len(self.layers)-1,upto,-1):
            next_grad = self.layers[i-1].bprop(next_grad)
        
        return next_grad
    
    def classification_error(self, X, Y):
        """ Calculate error on the given data 
            assuming they are classes that should be predicted. 
        """
        Y_pred = unhot(self.predict(X))
        error = Y_pred != Y
        return np.mean(error)
    
    def sgd_epoch(self, X, Y, learning_rate, batch_size):
        n_samples = X.shape[0]
        n_batches = n_samples // batch_size
        X_total_batches = np.array_split(X,n_batches)
        Y_total_batches = np.array_split(Y,n_batches)
        for b in range(n_batches):
            
            X_batch = X_total_batches[b]
            Y_batch = Y_total_batches[b]
                # TODO: then forward and backward propagation + updates
            y_batch_pred = self.predict(X_batch)
            print("the y predict is",y_batch_pred)
            gradient = self.backpropagate(Y_batch,y_batch_pred) 
        
            #saving error at the end of the training set
            for layer in self.layers[-2:0:-1]:
                W, b = layer.params()
                dW, db = layer.grad_params()
                
                layer.W = layer.W - learning_rate * dW
                layer.b = layer.b - learning_rate * db
            
    
    def gd_epoch(self, X, Y):
        
        self.backpropagate(Y,self.predict(X))
        
        for i in range(1, len(self.layers)-1):
            
            W,b = self.layers[i].params()
            dW, db = layer.grad_params()
            layer.W = layer.W - learning_rate * dW
            layer.b = layer.b - learning_rate * db
            
            
    
    def train(self, X, Y, X_valid, Y_valid, learning_rate=0.1, max_epochs=100, batch_size=64,
              descent_type="sgd", y_one_hot=True):

        """ Train network on the given data. """
        n_samples = X.shape[0]
        n_batches = n_samples // batch_size
        if y_one_hot:
            Y_train = one_hot(Y)
        else:
            Y_train = Y
        print("... starting training")
        for e in range(max_epochs+1):
            if descent_type == "sgd":
                self.sgd_epoch(X, Y_train, learning_rate, batch_size)
            elif descent_type == "gd":
                self.gd_epoch(X, Y_train, learning_rate)
            else:
                raise NotImplementedError("Unknown gradient descent type {}".format(descent_type))

            # Output error on the training data
            train_loss = self._loss(X, Y_train)
            train_error = self.classification_error(X, Y)
            print('epoch {:.4f}, loss {:.4f}, train error {:.4f}'.format(e, train_loss, train_error))
            #output error on the validation data
            valid_loss = self._loss(X_valid,Y_valid)
            valid_error = self.classification_error(X_valid,Y_valid)
            print('epoch {:.4f}, valid_loss {:.4f}, valid_error {:.4f}'.format(e, valid_loss, valid_error))
            
    
    def check_gradients(self, X, Y):
        """ Helper function to test the parameter gradients for
        correctness. """
        for l, layer in enumerate(self.layers):
            if isinstance(layer, Parameterized):
                print('checking gradient for layer {}'.format(l))
                for p, param in enumerate(layer.params()):
                    # we iterate through all parameters
                    param_shape = param.shape
                    # define functions for conveniently swapping
                    # out parameters of this specific layer and 
                    # computing loss and gradient with these 
                    # changed parametrs
                    def output_given_params(param_new):
                        """ A function that will compute the output 
                            of the network given a set of parameters
                        """
                        # copy provided parameters
                        param[:] = np.reshape(param_new, param_shape)
                        # return computed loss
                        return self._loss(X, Y)

                    def grad_given_params(param_new):
                        """A function that will compute the gradient 
                           of the network given a set of parameters
                        """
                        # copy provided parameters
                        param[:] = np.reshape(param_new, param_shape)
                        # Forward propagation through the net
                        Y_pred = self.predict(X)
                        # Backpropagation of partial derivatives
                        self.backpropagate(Y, Y_pred, upto=l)
                        # return the computed gradient 
                        return np.ravel(self.layers[l].grad_params()[p])

                    # let the initial parameters be the ones that
                    # are currently placed in the network and flatten them
                    # to a vector for convenient comparisons, printing etc.
                    param_init = np.ravel(np.copy(param))
                    
                    # To debug you network's gradients use scipys
                    # gradient checking!
                    epsilon = 1e-5
                    import scipy.optimize
                    err = scipy.optimize.check_grad(output_given_params, 
                          grad_given_params, param_init) 
                    print('diff scipy {:.2e}'.format(err))
                    assert(err < epsilon)
                    
                    # reset the parameters to their initial values
                    param[:] = np.reshape(param_init, param_shape)

# Gradient Checking
After implementing everything it is always a good idea to setup some layers and perform gradient
checking on random data. **Note** that this is only an example! It is not a useful network architecture ;). We also expect you to play around with this to test all your implemented components.

In [5]:
input_shape = (5, 10)
n_labels = 6
layers = [InputLayer(input_shape)]

layers.append(FullyConnectedLayer(
                layers[-1],
                num_units=15,
                init_stddev=0.1,
                activation_fun=Activation('relu')
))
layers.append(FullyConnectedLayer(
                layers[-1],
                num_units=6,
                init_stddev=0.1,
                activation_fun=Activation('tanh')
))
layers.append(FullyConnectedLayer(
                layers[-1],
                num_units=n_labels,
                init_stddev=0.1,
                activation_fun=Activation('relu')
))
layers.append(SoftmaxOutput(layers[-1]))
nn = NeuralNetwork(layers)

In [6]:
# create random data
X = np.random.normal(size=input_shape)
# and random labels
Y = np.zeros((input_shape[0], n_labels))
for i in range(Y.shape[0]):
    idx = np.random.randint(n_labels)
    Y[i, idx] = 1.

In [7]:
nn.check_gradients(X, Y)

checking gradient for layer 1
called fprop
called fprop
called fprop
called bprop
called bprop
called bprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called fprop
called f

# Training on MNIST
Finally we can let our network run on the MNIST dataset!

First load the data and reshape it.

In [8]:
# load
Dtrain, Dval, Dtest = mnist()
X_train, y_train = Dtrain
X_valid, y_valid = Dval

... loading data
... done loading data


*Dtrain* contains 50k images which are of size 28 x 28 pixels. Hence:

In [9]:
print("X_train shape: {}".format(np.shape(X_train)))
print("y_train shape: {}".format(np.shape(y_train)))

X_train shape: (50000, 1, 28, 28)
y_train shape: (50000,)


y_train will automatically be converted in the *train()* function to one_hot encoding.


But we need to reshape X_train, as our Network expects flat vectors of size 28*28 as input!

In [10]:
X_train = X_train.reshape(X_train.shape[0], -1)
print("Reshaped X_train size: {}".format(X_train.shape))
X_valid = X_valid.reshape((X_valid.shape[0], -1))
print("Reshaped X_valid size: {}".format(X_valid.shape))

Reshaped X_train size: (50000, 784)
Reshaped X_valid size: (10000, 784)


Ah, much better ;-)! 

Now we can finally really start training a Network!


I pre-defined a small Network for you below. Again This is not really a good default and will not produce state of the art results. Please play around with this a bit. See how different activation functions and training procedures (gd / sgd) affect the result.

In [11]:
import time

# Setup a small MLP / Neural Network
# we can set the first shape to None here to indicate that
# we will input a variable number inputs to the network
input_shape = (None, 28*28)
layers = [InputLayer(input_shape)]
layers.append(FullyConnectedLayer(
                layers[-1],
                num_units=100,
                init_stddev=0.01,
                activation_fun=Activation('relu')
))
layers.append(FullyConnectedLayer(
                layers[-1],
                num_units=100,
                init_stddev=0.01,
                activation_fun=Activation('relu')
))
layers.append(FullyConnectedLayer(
                layers[-1],
                num_units=10,
                init_stddev=0.01,
                # last layer has no nonlinearity 
                # (softmax will be applied in the output layer)
                activation_fun=None 
))
layers.append(SoftmaxOutput(layers[-1]))

nn = NeuralNetwork(layers)
# Train neural network
t0 = time.time()
nn.train(X_train, y_train, X_valid, y_valid, learning_rate=0.1, 
         max_epochs=20, batch_size=64, y_one_hot=True)
t1 = time.time()
print('Duration: {:.1f}s'.format(t1-t0))

... starting training
called fprop
called fprop
called fprop
the y predict is [[0.09961313 0.10066801 0.09971876 0.10104191 0.09974734 0.09814153
  0.10109973 0.10045805 0.10039825 0.09911328]
 [0.09968142 0.10066402 0.09972075 0.10107123 0.09978709 0.09814283
  0.1010377  0.10043638 0.10031322 0.09914537]
 [0.09966212 0.10070612 0.09971155 0.10111788 0.09972998 0.0981063
  0.10105738 0.10042954 0.10038286 0.09909627]
 [0.09967404 0.10069592 0.09972606 0.10111707 0.09974766 0.09809692
  0.10106227 0.10042435 0.10035194 0.09910377]
 [0.09963514 0.10073138 0.09970855 0.10112073 0.09975733 0.09813817
  0.10103752 0.10040595 0.10034561 0.09911963]
 [0.09965215 0.10069704 0.09971351 0.10111942 0.0997675  0.09807036
  0.10107028 0.10039624 0.1003665  0.09914699]
 [0.09965384 0.1007228  0.09973022 0.10113177 0.09973163 0.09810776
  0.10106716 0.10038214 0.10035374 0.09911893]
 [0.09962429 0.10072363 0.09970955 0.10107805 0.09972084 0.09815029
  0.10104834 0.10043846 0.10038415 0.09912239]
 [0

called fprop
called fprop
called fprop
the y predict is [[0.10043853 0.10195407 0.09925307 0.10099995 0.0997119  0.09710546
  0.10117895 0.10044637 0.09978249 0.09912922]
 [0.10038802 0.10197861 0.09931584 0.1011141  0.0997554  0.0970505
  0.10117669 0.10037488 0.09973106 0.09911488]
 [0.10042366 0.10195147 0.09927785 0.10106964 0.09971681 0.09709445
  0.10119119 0.10038064 0.09974888 0.09914541]
 [0.10040588 0.10197867 0.0992444  0.10109197 0.09973565 0.09708939
  0.10117028 0.10038588 0.09977169 0.09912618]
 [0.100404   0.10196143 0.09927488 0.10105474 0.09973462 0.09708508
  0.10122146 0.10041848 0.09974057 0.09910474]
 [0.10040704 0.10195281 0.09927263 0.10104651 0.09972182 0.09712334
  0.10118377 0.10041288 0.09975244 0.09912676]
 [0.10039912 0.10193564 0.0993197  0.10105443 0.09974786 0.09708622
  0.10117444 0.10037763 0.09976948 0.09913548]
 [0.10043695 0.10193163 0.09926972 0.10107042 0.09976052 0.09706936
  0.10115089 0.10043554 0.09977538 0.0990996 ]
 [0.100518   0.10186774 0

  0.10034948 0.10082714 0.09884297 0.09992709]]
called bprop
called bprop
called bprop
called fprop
called fprop
called fprop
the y predict is [[0.09958874 0.102696   0.09996077 0.10091974 0.10045164 0.09670055
  0.10029332 0.10062278 0.09877557 0.0999909 ]
 [0.09958663 0.10270931 0.09996753 0.10090321 0.10046871 0.09672653
  0.10024686 0.10059714 0.09878838 0.10000569]
 [0.09955312 0.10268556 0.10005497 0.10095431 0.10042642 0.09667594
  0.10029564 0.10054639 0.09877849 0.10002914]
 [0.09970095 0.10261996 0.10005219 0.10083643 0.10046052 0.09672999
  0.10025871 0.10058212 0.09873518 0.10002397]
 [0.09954128 0.10274174 0.09997105 0.10090728 0.10043161 0.09671063
  0.10029568 0.10062124 0.09878522 0.09999427]
 [0.0995599  0.10272266 0.09999884 0.10099503 0.1004616  0.0966726
  0.10026194 0.10057757 0.09874605 0.1000038 ]
 [0.09956401 0.10269308 0.10002005 0.1009035  0.10044055 0.09670304
  0.10031674 0.10058337 0.09875168 0.10002398]
 [0.09972787 0.10262857 0.10007168 0.10078332 0.10045

  0.0998815  0.10125598 0.09855884 0.1000762 ]]
called bprop
called bprop
called bprop
called fprop
called fprop
called fprop
the y predict is [[0.0997591  0.10367257 0.10073722 0.10023742 0.09997443 0.09697949
  0.09981751 0.10102636 0.09823204 0.09956385]
 [0.09978323 0.1036453  0.10079815 0.10022915 0.09999592 0.09691777
  0.09982944 0.10099462 0.09824527 0.09956115]
 [0.09975803 0.10367026 0.10079935 0.10022218 0.09999082 0.0969525
  0.09982125 0.10102504 0.09816836 0.09959221]
 [0.09971742 0.10366975 0.10078796 0.10025459 0.09997087 0.09696834
  0.09983346 0.10104083 0.09824424 0.09951254]
 [0.09981806 0.10363775 0.10077676 0.1002814  0.10001078 0.09698293
  0.09977266 0.10098971 0.0981789  0.09955106]
 [0.09974016 0.10370917 0.10074074 0.10027109 0.09998666 0.09695624
  0.09981634 0.10104363 0.09822286 0.09951312]
 [0.09980711 0.10360991 0.10075484 0.10026339 0.10000487 0.09697171
  0.09982184 0.10101485 0.09818757 0.09956391]
 [0.09976427 0.10365553 0.10078571 0.10022612 0.10002

called fprop
called fprop
called fprop
the y predict is [[0.09953639 0.10287233 0.09960595 0.09963782 0.10067918 0.0972256
  0.09956081 0.1030751  0.09862599 0.09918083]
 [0.09942789 0.10291635 0.09958219 0.09975945 0.1006801  0.09715104
  0.0996124  0.103039   0.09864006 0.09919152]
 [0.09935456 0.10300812 0.09957525 0.09971916 0.10066598 0.09716784
  0.09958186 0.10309777 0.09867882 0.09915063]
 [0.09945444 0.10293261 0.0996336  0.0997104  0.10068334 0.09717975
  0.0995501  0.10306818 0.09862854 0.09915905]
 [0.09938598 0.10296156 0.09957619 0.09971551 0.10067119 0.09718805
  0.09958171 0.1031074  0.09864794 0.09916447]
 [0.09944313 0.10291709 0.09958599 0.09966249 0.10064684 0.09720892
  0.09958902 0.10311614 0.09868808 0.09914231]
 [0.0994203  0.10291624 0.09957431 0.09970171 0.1006679  0.09723925
  0.09960098 0.10311892 0.09860196 0.09915842]
 [0.09944456 0.1028891  0.09960292 0.09967824 0.10069492 0.09716298
  0.09961463 0.10308303 0.09865516 0.09917445]
 [0.09940581 0.10292802 0

...

  3.85766285e-04 4.46946384e-03]]
called bprop
called bprop
called bprop
called fprop
called fprop
called fprop
the y predict is [[7.74813807e-02 5.70810812e-05 7.96518159e-03 2.49911415e-01
  1.87483654e-04 5.43444998e-01 6.17601290e-04 1.79417522e-03
  1.15264393e-01 3.27629125e-03]
 [1.33567689e-07 8.83775320e-03 9.23541003e-01 5.68859540e-02
  3.03906636e-08 1.92447899e-04 8.60672852e-05 5.90303394e-07
  1.04557415e-02 2.78983594e-07]
 [3.51452440e-05 2.70842448e-04 5.97427247e-04 6.22137857e-04
  6.05240962e-01 1.53813469e-02 2.44970817e-03 7.60471835e-03
  3.23906380e-02 3.35407074e-01]
 [9.06710338e-01 3.31950428e-11 2.03625655e-05 6.31209481e-04
  3.03619321e-07 9.18735418e-02 2.74250210e-05 5.92614216e-08
  7.35940569e-04 8.19832701e-07]
 [1.29471443e-05 5.61339922e-04 7.65915945e-05 2.26077875e-03
  4.00226471e-03 4.80004352e-03 4.10451052e-06 7.61951197e-01
  7.49392928e-03 2.18836804e-01]
 [5.57618886e-09 6.17895333e-09 2.66494577e-07 1.66873167e-08
  9.91292237e-01 6.57742

  4.24782217e-01 1.90151957e-02]]
called bprop
called bprop
called bprop
called fprop
called fprop
called fprop
the y predict is [[6.52917941e-08 2.00486119e-03 9.69476746e-05 1.74473653e-03
  1.33509939e-04 3.67603235e-04 8.32413813e-08 9.43017508e-01
  4.52038329e-03 4.81143019e-02]
 [1.48617365e-06 8.20722073e-01 5.26211329e-02 3.87117351e-02
  2.18594326e-04 1.43641429e-03 1.01672537e-04 5.98117545e-02
  2.17405479e-02 4.63458959e-03]
 [1.88140966e-04 3.71475009e-05 4.36193665e-03 9.59931173e-01
  1.38365426e-07 2.01551162e-02 3.09269578e-07 6.43137111e-04
  1.45524898e-02 1.30411424e-04]
 [6.04986853e-05 8.66222504e-03 1.38103982e-03 1.25980224e-02
  2.47259796e-03 6.37225593e-03 2.53785419e-05 8.62811139e-01
  1.33163997e-02 9.23004424e-02]
 [2.52329169e-06 2.80574144e-04 2.57696087e-04 7.78192370e-04
  1.89722766e-01 8.17501503e-03 7.73115630e-05 5.29758162e-02
  3.11053725e-02 7.16624733e-01]
 [3.85479106e-06 5.23037337e-05 2.25867863e-02 9.67475396e-01
  6.15710765e-10 2.28959

called bprop
called bprop
called bprop
called fprop
called fprop
called fprop
the y predict is [[1.28012572e-03 4.57673612e-04 7.78230382e-04 3.93309241e-03
  1.60219128e-01 7.37487291e-02 1.08989303e-03 1.35173710e-01
  2.25426217e-02 6.00776796e-01]
 [4.58247038e-06 1.54722758e-02 1.62995680e-01 1.93792866e-01
  1.24378184e-05 2.75973462e-02 7.86150393e-05 2.35743136e-03
  5.94496902e-01 3.19186315e-03]
 [1.08119663e-01 1.01137368e-04 2.49839600e-02 1.41683820e-01
  1.08974195e-03 5.89774549e-01 5.45732636e-03 9.50533833e-04
  1.20158454e-01 7.68081448e-03]
 [2.71473493e-05 4.52812271e-05 4.72468590e-04 5.90326355e-04
  1.35599421e-01 5.03845497e-02 7.08382860e-04 7.11644141e-03
  8.40941336e-02 7.20961848e-01]
 [7.35221298e-07 1.61190119e-06 5.09213238e-02 9.67194671e-02
  8.58251999e-09 3.05670219e-02 3.34225126e-06 1.15667144e-07
  8.21776289e-01 1.00840921e-05]
 [9.83164671e-01 1.95124635e-11 1.34033588e-05 1.04985528e-03
  1.33837477e-09 1.56847189e-02 7.80360920e-07 2.25398828e

called fprop
called fprop
called fprop
called fprop
called fprop
epoch 0.0000, loss 0.5247, train error 0.1561
called fprop
called fprop
called fprop


ValueError: operands could not be broadcast together with shapes (10000,10) (10000,) 

# Figure out a reasonable Network that achieves good performance
As the last part of this task, setup a network that works well and gets reasonable accuracy, say ~ 1-3 percent error on the **validation set**. 
Train this network on the complete data and compute the **test error**. 

Visualize the validation loss and training loss for each iteration in a plot, e.g. using matplotlib

In [ ]:
X_t, Y_test = Dtest
X_test = X_t.reshape(X_t.shape[0], -1)
Y_pred = nn.predict(X_test)

error = nn.classification_error(X_test, Y_test)
print('Test error: {:.5f}' .format(error))

errors_per_number = np.zeros(10)
unhotted = unhot(Y_pred)
for i in range(len(unhotted)):
    if unhotted[i] != Y_test[i]:
        errors_per_number[Y_test[i]] += 1
print('Errors per number: ')
print(errors_per_number)
often_bad = np.argmax(errors_per_number)
often_good = np.argmin(errors_per_number)
print('Number most often classified correctly: {}' .format(often_good))
print('Number most often classified incorrectly: {}' .format(often_bad))

import heapq
diff = np.abs(Y_pred - one_hot(Y_test)).flatten()
print('Best results at: ')
best_five = diff.argsort()[0:5]

def show_image(im):
    two_d = (np.reshape(im, (28, 28)) * 255).astype(np.uint8)
    plt.imshow(two_d, interpolation='nearest')
    plt.show()
    
for i in range(5):
    show_image(X_t[best_five[i]//10, :, : ,:])

print('Off by the most at: ')
worst_five = diff.argsort()[-6:]

for i in range(5):
    show_image(X_t[worst_five[i]//10, :, : ,:])
